## Miscellaneous notebook

In [1]:
# # TF's recommender imports
# !pip install -q tensorflow-recommenders
# !pip install -q tensorflow_ranking
# !pip install -q --upgrade tensorflow-datasets
# !pip install -q scann

In [2]:
import pandas as pd
import nltk
nltk.download('punkt')
from nltk.corpus import stopwords
import re
import numpy as np
import pickle
from nltk.tokenize import RegexpTokenizer, word_tokenize
import io
from collections import defaultdict
import os
import pprint
import tempfile
from typing import Dict, Text
import numpy as np
# import tensorflow as tf
# import tensorflow_datasets as tfds
# import tensorflow_recommenders as tfrs
# import tensorflow_ranking as tfr

[nltk_data] Downloading package punkt to
[nltk_data]     /Users/nicolemichaud/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [3]:
user_data = pd.read_csv('data/RAW_interactions.csv')

recipe_data = pd.read_csv('data/RAW_recipes.csv')

# recipes_PP = pd.read_csv('data/PP_recipes.csv')

# users_PP = pd.read_csv('data/PP_users.csv')

# pickled_map = pd.read_pickle('data/ingr_map.pkl')

In [66]:
# Creating a function to perform cleaning steps at once
stopwords_list = stopwords.words('english')

no_bad_chars = re.compile('[!\"#$%&()*+-./:;<=>?@[\]^_`{|}~\n - ]')
no_nums = re.compile('[\d-]')

def clean_text(text):
    text = no_nums.sub('', text) 
    text = no_bad_chars.sub(' ', text) 
    text = text.lower() 
    text = ' '.join(word for word in text.split() if word not in stopwords_list)
    return text


In [67]:
recipe_data['description'] = recipe_data['description'].astype(str)
descr_cleaned = recipe_data['description'].apply(clean_text)

recipe_data['name'] = recipe_data['name'].astype(str)
names_cleaned = recipe_data['name'].apply(clean_text)

tags_cleaned = recipe_data['tags'].apply(clean_text)

##### Seeing which text columns contain the most information about each diet type (vegetarian, vegan, and gluten-free):

In [6]:
# how many recipe names include the word 'vegetarian'?
len(names_cleaned[names_cleaned.str.contains('vegetarian')])


928

In [7]:
# how many recipe descriptions include the word 'vegetarian'?
len(descr_cleaned[descr_cleaned.str.contains('vegetarian')])

3784

In [8]:
# how many recipe names include the word 'vegan'?
len(names_cleaned[names_cleaned.str.contains('vegan')])

1362

In [9]:
# how many recipe descriptions include the word 'vegan'?
len(descr_cleaned[descr_cleaned.str.contains('vegan')])

1909

In [10]:
len(recipe_data[recipe_data['ingredients'].str.contains('vegetarian')])


293

In [11]:
len(recipe_data[recipe_data['ingredients'].str.contains('vegan')])


367

In [12]:
len(recipe_data[recipe_data['ingredients'].str.contains('gluten-free')])


305

In [13]:
len(recipe_data[recipe_data['ingredients'].str.contains('gluten free')])


54

In [14]:
len(recipe_data[recipe_data['name'].str.contains('gluten-free')])


0

In [15]:
len(recipe_data[recipe_data['name'].str.contains('gluten free')])


939

In [16]:
len(recipe_data[recipe_data['description'].str.contains('gluten free')])


571

In [17]:
len(recipe_data[recipe_data['tags'].str.contains('gluten-free')])

5743

In [18]:
len(recipe_data[recipe_data['tags'].str.contains('vegan')])

10012

In [18]:
recipe_data[recipe_data['tags'].str.contains('vegan')]

name      id  minutes  \
6                                   aww  marinated olives   25274       15   
19                      cream  of cauliflower soup  vegan   23850      110   
21                          cream  of spinach soup  vegan   24701       55   
26                            fool the meat eaters  chili   54272       40   
61                        mock a mole   low fat guacamole   81185       15   
...                                                   ...     ...      ...   
231559  zucchini  courgettes sauteed with sun dried to...  413205       40   
231566                                            zucotte   96811       65   
231572                                       zulu cabbage  455000       40   
231610                   zurie s overnight no knead bread  196201       70   
231633                                   zydeco spice mix  493372        5   

        contributor_id   submitted  \
6                21730  2002-04-14   
19                3288  2002-03-28   
21                3288  2002-04-08   
26               40525  2003-02-17   
61               67026  2004-01-15   
...                ...         ...   
231559          485109  2010-02-16   
231566           65056  2004-08-03   
231572         1058097  2011-05-04   
231610          200862  2006-11-18   
231633         1500678  2013-01-09   

                                                     tags  \
6       ['15-minutes-or-less', 'time-to-make', 'course...   
19      ['lactose', 'weeknight', 'time-to-make', 'cour...   
21      ['60-minutes-or-less', 'time-to-make', 'course...   
26      ['60-minutes-or-less', 'time-to-make', 'course...   
61      ['15-minutes-or-less', 'time-to-make', 'course...   
...                                                   ...   
231559  ['weeknight', '60-minutes-or-less', 'time-to-m...   
231566  ['time-to-make', 'course', 'main-ingredient', ...   
231572  ['60-minutes-or-less', 'time-to-make', 'course...   
231610  ['time-to-make', 'course', 'main-ingredient', ...   
231633  ['15-minutes-or-less', 'time-to-make', 'course...   

                                          nutrition  n_steps  \
6          [380.7, 53.0, 7.0, 24.0, 6.0, 24.0, 6.0]        4   
19         [174.2, 4.0, 24.0, 1.0, 15.0, 1.0, 10.0]       10   
21           [64.8, 3.0, 13.0, 54.0, 4.0, 2.0, 3.0]       10   
26        [295.6, 3.0, 56.0, 76.0, 32.0, 1.0, 18.0]        9   
61          [115.9, 7.0, 21.0, 19.0, 9.0, 3.0, 5.0]        7   
...                                             ...      ...   
231559       [115.4, 7.0, 33.0, 6.0, 8.0, 3.0, 5.0]       12   
231566     [145.7, 13.0, 10.0, 2.0, 3.0, 27.0, 5.0]       10   
231572        [94.0, 7.0, 25.0, 4.0, 4.0, 3.0, 4.0]        5   
231610  [1379.6, 5.0, 12.0, 194.0, 79.0, 3.0, 96.0]       82   
231633        [14.8, 0.0, 2.0, 58.0, 1.0, 0.0, 1.0]        1   

                                                    steps  \
6       ['toast the fennel seeds and lightly crush the...   
19      ['heat the oil or margarine in a soup pot and ...   
21      ['in a 3 qt saucepan over medium high heat , s...   
26      ['rehydrate tvp if needed', 'spray or oil a la...   
61      ['thaw peas by running hot water over them in ...   
...                                                   ...   
231559  ['place the sundried tomatoes in the 3 / 4 cup...   
231566  ['in a large , heavy saucpan , melt 1 tbs of t...   
231572  ['heat the oil in a large skillet', 'add onion...   
231610  ["since first making this bread according to t...   
231633        ['mix all ingredients together thoroughly']   

                                              description  \
6       my italian mil was thoroughly impressed by my ...   
19                                  this is a dairy free    
21      thickened with a mix of cooked oats and vegies...   
26      this recipe was adapted by my mother and mysel...   
61                           from crescent dragonwagon's    
...                                                   ... 

In [19]:
len(recipe_data[recipe_data['tags'].str.contains('vegetarian')])

35651

In [20]:
#print(recipe_data[recipe_data['name'].str.contains('gluten free')])

In [21]:
len(recipe_data[recipe_data['description'].str.contains('gluten-free')])


473

In [21]:
len(recipe_data['description'].isin(gluten_free))

231637

In [22]:
len(recipe_data[recipe_data['description'].str.contains("vegetarian")])

3784

In [23]:
len(recipe_data[recipe_data['description'].str.contains("gluten free")])

571

In [24]:
len(recipe_data[recipe_data['description'].str.contains("gluten-free")])

473

The different columns for vegan and vegetarian are not very consistent, so it is better to filter through the ingredients to classify those diet-types. The 'tags' column contains the most information about the gluten-free diet-type.

In [ ]:
#make histogram showing value counts of each diet word in each column to show decision

In this project, vegetarian is defined as not containing meat or seafood but can contain eggs and dairy. Vegan is defined as not containing any animal products.

In [19]:
# creating ingredient lists to filter out for each diet type

meat = ['ham', 'beef', 'meat', 'chicken', 'pork', 'bacon', 'sausage', 'lamb', 'veal', 'turkey', 'steak', 'rib', 'frankfurter', 'duck', 'poultry', 'goat', 'liver', 'hen', 'quail', 'brisket', 'goose']
seafood = ['fish', 'shrimp', 'seafood', 'crab', 'lobster', 'clam', 'oyster', 'scallop', 'mussel', 'cod', 'salmon', 'halibut', 'shellfish', 'roe', 'tuna', 'caviar', 'pollock', 'yellowtail', 'squid', 'calamari', 'octopus', 'crawfish', 'crayfish', 'sardine', 'trout', 'flounder', 'anchovy', 'bass', 'haddock', 'sole' ]
animal_other = ['egg', 'honey']
dairy = ['milk', 'cheese', 'yogurt', 'mayonnaise', 'butter', 'margarine', 'cream']
gluten_free = ['gluten free', 'gluten-free']


In [20]:
# condensing those ingredient lists for the vegan and vegetarian diet type
vegan = ['ham', 'beef', 'meat', 'chicken', 'pork', 'bacon', 'sausage', 'lamb', 'veal', 'turkey', 'steak', 'rib', 'frankfurter', 'duck', 'poultry', 'goat', 'liver', 'hen', 'quail', 'brisket', 'goose','fish', 'shrimp', 'seafood', 'crab', 'lobster', 'clam', 'oyster', 'scallop', 'mussel', 'cod', 'salmon', 'halibut', 'shellfish', 'roe', 'tuna', 'caviar', 'pollock', 'yellowtail', 'squid', 'calamari', 'octopus', 'crawfish', 'crayfish', 'sardine', 'trout', 'flounder', 'anchovy', 'bass', 'haddock', 'sole','egg', 'honey','milk', 'cheese', 'yogurt', 'mayonnaise', 'butter', 'margarine', 'cream']

vegetarian = ['ham', 'beef', 'meat', 'chicken', 'pork', 'bacon', 'sausage', 'lamb', 'veal', 'turkey', 'steak', 'rib', 'frankfurter', 'duck', 'poultry', 'goat', 'liver', 'hen', 'quail', 'brisket', 'goose','fish', 'shrimp', 'seafood', 'crab', 'lobster', 'clam', 'oyster', 'scallop', 'mussel', 'cod', 'salmon', 'halibut', 'shellfish', 'roe', 'tuna', 'caviar', 'pollock', 'yellowtail', 'squid', 'calamari', 'octopus', 'crawfish', 'crayfish', 'sardine', 'trout', 'flounder', 'anchovy', 'bass', 'haddock', 'sole']


In [32]:
#Create ratings distribution

from plotly.offline import init_notebook_mode, plot, iplot
import plotly.graph_objs as go
init_notebook_mode(connected=True)

data = user_data['rating'].value_counts().sort_index(ascending=False)
trace = go.Bar(x = data.index,
               text = ['{:.1f} %'.format(val) for val in (data.values / user_data.shape[0] * 100)],
               textposition = 'auto',
               textfont = dict(color = '#000000'),
               y = data.values,
               )
# Create layout
layout = dict(title = 'Distribution Of {} Recipe Ratings'.format(user_data.shape[0]),
              xaxis = dict(title = 'Rating'),
              yaxis = dict(title = 'Count'))
# Create plot
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)
#view raw

In [86]:
# Number of ratings per recipe
data = user_data.groupby('recipe_id')['user_id'].count()

# Create trace
trace = go.Histogram(x = data.values,
                     name = 'Ratings',
                     xbins = dict(start = 0,
                                  end = 25,
                                  size = 2))
# Create layout
layout = go.Layout(title = 'Distribution of Number of Ratings Per Recipe (Clipped at 25)',
                   xaxis = dict(title = 'Number of Ratings Per Recipe'),
                   yaxis = dict(title = 'Count'),
                   bargap = 0.2)

# Create plot
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)
print(min(data.value_counts()))
print(max(data.value_counts()))

1
91953


In [76]:
recipe_data_counts = user_data.groupby('recipe_id')['rating'].count().reset_index(name='Count').sort_values(['Count'], ascending=False) 

In [88]:
max(recipe_data_counts['Count'])

1613

In [34]:
# user_data.groupby('recipe_id')['rating'].count().reset_index().sort_values('rating', ascending=False)[:10]

In [83]:
# Number of ratings per user
data = user_data.groupby('user_id')['recipe_id'].count()

# Create trace
trace = go.Histogram(x = data.values,
                     name = 'Ratings',
                     xbins = dict(start = 0,
                                  end = 25,
                                  size = 2))
# Create layout
layout = go.Layout(title = 'Distribution Of Number of Ratings Per User (Clipped at 25)',
                   xaxis = dict(title = 'Ratings Per User'),
                   yaxis = dict(title = 'Count'),
                   bargap = 0.2)

# Create plot
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)
print(min(data))
print(max(data))

1
7671


In [89]:
user_review_counts = user_data.groupby('user_id')['recipe_id'].count().reset_index(name='Count').sort_values(['Count'], ascending=False) 
max(user_review_counts['Count'])


7671

The minimum amount of recipes a user has reviewed is 1 recipe, the maximum number of recipes a user has review is 50 recipes.

In [46]:
# user_data.groupby('user_id')(len['rating']).reset_index().sort_values('rating', ascending=False)[:10]

In [55]:
tags_cleaned = tags_cleaned.astype(str)


In [56]:
# tokenizer = word_tokenize()
tag_tokens = word_tokenize(tags_cleaned)

TypeError: expected string or bytes-like object

In [44]:
# most common tags?
top_tags = tags_cleaned.value_counts()[:10].sort_values(ascending=False)
top_tags

NameError: name 'tags_cleaned' is not defined

In [68]:
# from medium post
import nltk
vocabulary = nltk.FreqDist()
# This was done once I had already preprocessed the ingredients
for ingredients in recipe_data['ingredients']:
    ingredients = ingredients.split()
    vocabulary.update(ingredients)
for word, frequency in vocabulary.most_common(20):
    print(f'{word};{frequency}')

'salt',;78127
'fresh;69489
pepper',;69038
oil',;63883
cheese',;56768
'garlic;48915
powder',;48872
sauce',;40913
'ground;40293
'butter',;38862
'sugar',;38756
sugar',;38724
'onion',;35739
juice',;35263
'baking;32393
flour',;30848
cloves',;28912
'eggs',;28726
'red;28284
'dried;27365


In [69]:
# from medium post
import nltk
vocabulary = nltk.FreqDist()
# This was done once I had already preprocessed the ingredients
for tag in tags_cleaned:
    tag = tag.split()
    vocabulary.update(tag)
for word, frequency in vocabulary.most_common(50):
    print(f'{word};{frequency}')

'preparation';230546
'timetomake';225326
'course';218148
'mainingredient';170446
'minutesorless';169001
'dietary';165091
'easy';126062
'occasion';114145
'cuisine';91165
'lowinsomething';85776
'maindish';71786
'equipment';70436
'healthy';66959
'numberofservings';58949
'meat';56042
'vegetables';53814
'tastemood';52143
'hoursorless';49497
'northamerican';48479
'stepsorless';44933
'lowsodium';43349
'desserts';43203
'lowcarb';42189
'dinnerparty';37561
'lowcholesterol';36743
'lowcalorie';36429
'vegetarian';35651
'beginnercook';35561
'ingredientsorless';35466
'holidayevent';34920
'inexpensive';32619
'lowprotein';32522
'lowsaturatedfat';31378
'fruit';31324
'oven';31180
'american';31179
'eggsdairy';30142
'pastariceandgrains';27084
'kidfriendly';27074
'sidedishes';26902
'comfortfood';26136
'european';24912
'presentation';24470
'poultry';24160
'lunch';23800
'foror';23084
'lowfat';22170
'stovetop';22095
'seasonal';21933
'weeknight';20948
